In [1]:
import pandas as pd
import os
import re

import string

chars = string.ascii_letters + string.punctuation + string.whitespace
chars = chars + "éèê"

url_pattern = r"(http|https)\S*"
user_naming_pattern = r"@\S*"

In [27]:
mlma_dataset = "../../data/hate_speech_mlma_fr_dataset.csv"
output_dir = "../../data/processed/"

mlma_df = pd.read_csv(mlma_dataset, index_col=[0])

In [3]:
mlma_df.tweet = mlma_df.tweet.apply(lambda x: re.sub(user_naming_pattern, "", x).strip())

mlma_abuse_df = mlma_df \
    .loc[mlma_df.sentiment != "normal"]

mlma_no_abuse_df = mlma_df \
    .loc[mlma_df.sentiment == "normal"]

mlma_abuse_df

tweet  \
HITId                                                      
1      rt  personnage ainsi q tte la clique gauchiste...   
2           bah oui t'as raison l'autre c'est un mongol.   
3      moi j'ai personne à qui m'adresser pour réclam...   
6      en algerie les migrants sont expulsés dans le ...   
9      mytho t'as juste voulu te faire ken par les re...   
...                                                  ...   
4009   vos twt rappel l'époque ou les journalistes tr...   
4010   tres bien. le cinema francais c...est souvent ...   
4011         j’ai que des rebeus en demande d’amis aussi   
4012                                  sale juif de merde   
4014   mdr c’est un mongol lui en mode lui demander d...   

                  sentiment directness  \
HITId                                    
1                   abusive     direct   
2                 offensive   indirect   
3                   hateful     direct   
6                 offensive   indirect   
9                 offensive   indirect   
...                     ...        ...   
4009              offensive     direct   
4010              offensive   indirect   
4011   disrespectful_normal     direct   
4012              offensive     direct   
4014              offensive   indirect   

                           annotator_sentiment      target             group  
HITId                                                                         
1                                        shock      origin             other  
2                                        shock       other        individual  
3         anger_confusion_sadness_fear_disgust       other             women  
6                                 indifference       other        immigrants  
9                         indifference_disgust       other        individual  
...                                        ...         ...               ...  
4009                                     shock       other              jews  
4010                                   sadness       other  left_wing_people  
4011                              indifference      origin             arabs  
4012   fear_shock_indifference_sadness_disgust    religion              jews  
4014                              indifference  disability        individual  

[3193 rows x 6 columns]

In [17]:
def clean_text(text):
    
    out = text.replace("rt ", "")
    out = out.replace("\xa0", "")
    for w in out.split():
        if "…" in w:
            out = out.replace(w, "")
    return out

target_categories = ["abusive", "offensive"]
pruned_mlma_abuse = mlma_abuse_df.loc[mlma_abuse_df.sentiment.isin(target_categories)]
pruned_mlma_abuse.tweet = pruned_mlma_abuse.tweet.apply(clean_text)
pruned_mlma_abuse

/tmp/ipykernel_17576/1118330829.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pruned_mlma_abuse.tweet = pruned_mlma_abuse.tweet.apply(clean_text)


tweet  sentiment  \
HITId                                                                 
1       personnage ainsi q tte la clique gauchiste de...    abusive   
2           bah oui t'as raison l'autre c'est un mongol.  offensive   
6      en algerie les migrants sont expulsés dans le ...  offensive   
9      mytho t'as juste voulu te faire ken par les re...  offensive   
10     c’est un giga attardé mdrrr ils va vraiment se...  offensive   
...                                                  ...        ...   
4008              pk tu mparles ching chong fils de pute  offensive   
4009   vos twt rappel l'époque ou les journalistes tr...  offensive   
4010   tres bien. le cinema francais c...est souvent ...  offensive   
4012                                  sale juif de merde  offensive   
4014   mdr c’est un mongol lui en mode lui demander d...  offensive   

      directness                      annotator_sentiment      target  \
HITId                                                                   
1         direct                                    shock      origin   
2       indirect                                    shock       other   
6       indirect                             indifference       other   
9       indirect                     indifference_disgust       other   
10        direct                             indifference      origin   
...          ...                                      ...         ...   
4008      direct                             indifference      origin   
4009      direct                                    shock       other   
4010    indirect                                  sadness       other   
4012      direct  fear_shock_indifference_sadness_disgust    religion   
4014    indirect                             indifference  disability   

                  group  
HITId                    
1                 other  
2            individual  
6            immigrants  
9            individual  
10           individual  
...                 ...  
4008             asians  
4009               jews  
4010   left_wing_people  
4012               jews  
4014         individual  

[1930 rows x 6 columns]

In [28]:
pruned_mlma_abuse.to_csv(os.path.join(output_dir, "mlma_positive.csv"))
mlma_no_abuse_df.to_csv(os.path.join(output_dir, "mlma_negative.csv"))